In [81]:
#!pip install gensim

In [3]:
import gensim, operator
from scipy import spatial
import numpy as np
from gensim.models import KeyedVectors
import webhoseio, os
from gensim.models import KeyedVectors
import json
from simhash import Simhash, SimhashIndex
import numpy as np


# Load Word Vector Model¶

In [4]:
#word vector-based semantic deduplication on top of LSH. 
#The choice of word embedding model, 

model_path = '/Users/rissacao/downloads/'
def load_wordvec_model(modelName, modelFile, flagBin):
    print('Loading ' + modelName + ' model...')
    model = KeyedVectors.load_word2vec_format(model_path + modelFile, binary=flagBin)
    print('Finished loading ' + modelName + ' model...')
    return model

model_w2v_AP    = load_wordvec_model('Word2Vec Google News', 'GoogleNews-vectors-negative300.bin.gz', True)
#model_fasttext = load_wordvec_model('FastText', 'fastText_wiki_en.vec', False)

Loading Word2Vec Google News model...
Finished loading Word2Vec Google News model...


In [5]:
# function checks whether the input words are present in the vocabulary for the model
def vocab_check(vectors, words):
    
    output = list()
    for word in words:
        if word in vectors.vocab:
            output.append(word.strip())
            
    return output

In [6]:
# function calculates similarity between two strings using a particular word vector model
def calc_similarity(input1, input2, vectors):
    s1words = set(vocab_check(vectors, input1.split()))
    s2words = set(vocab_check(vectors, input2.split()))
    
    # Compute cosine similarity between two sets of words using a particular word vector model
    output = vectors.n_similarity(s1words, s2words)
    return output

In [7]:
def cleanup(input):
    # remove English stopwords
    input = input.replace("'s", " ").replace("n’t", " not").replace("’ve", " have")
    input = re.sub(r'[^a-zA-Z0-9 ]', '', input)
    return input

# Loads your previously obtained dataset of Webhose news articles 

In [8]:
import json 
    
#read data from json file
json_data=open("IBM_english.json").readlines()
#print(json_data)

#Output: print the number of articles, titles and publish dates of the first 100 articles.
feeds_read_from_file = []
for line in json_data:
    feeds_read_from_file.append(json.loads(line))
print(len(feeds_read_from_file))

#Print original dataset titles only
feeds = []
i = 0
for feed in feeds_read_from_file:
    feed['id'] = i
    print(feed['id'], str(feed['title']))
    i += 1
    feeds.append(feed)

6915
0 Two self-paced OpenShift Workshops for Developers
1 How Finding a Hobby Will Make You A Better Entrepreneur
2 Cognizant: Continued Strength Across Verticals, With 25% Stock Upside Likely In 2019-20 - Cognizant Technology Solutions Corporation (NASDAQ:CTSH)
3 Group Puzzles Out Silicon Specs
4 When AIs go to war: Autonomous cyber weapons ‘inevitable’
5 Tuesday Night
6 ROOMZ expands into the UK and Ireland
7 Digital skills are Africa’s ticket to prosperity
8 LevaData Announces 2019 Cognitive Sourcing Summit
9 Exeter Township woman began career in computer programming in 1962
10 Nutanix appoints new General Manager to oversee UK and Ireland
11 Why We Love Domain promo Code (And You Should, Too!)
12 Hedera Hashgraph Opens Public Network
13 Compute Express Link Consortium (CXL) Officially Incorporates; Announces Expanded Board of Directors
14 How to Personalize Digital Experiences in Finance (Paul Shumsky)
15 IBM DS8900F AFA Up to 6TB for Z Mainframes
16 TAU Launches New Quantum Scien

# Define distance, index using SimHash only, calculate duplicates subset using SimHash ¶

In [10]:
#Hamming distance – the number of positions at which the corresponding words differ.
#Define distance as 10, index using SimHash based on Hamming distance,the more similar the text inputs are, the smaller the Hamming distance of their hashes is 
distance = 10
#calculate duplicates subset using SimHash 
objs = [(str(feed['id']), Simhash(str(feed['title']))) for feed in feeds]
index = SimhashIndex(objs, k=distance)


In [11]:
# Select a feed from the list based on its index
SELECTED_INDEX = 71
feed_sel = feeds[SELECTED_INDEX]
print(feed_sel['title'])
# calculate  hash value
feed_hash = Simhash(str(feed_sel['title']))
# find all duplicate indices based on SimHash only
dup_indices = index.get_near_dups(feed_hash)
print("Number of duplicates (SimHash): " + str(len(dup_indices)))

count_dup = 0
for dupi in dup_indices:
    #print("(SimHash): " +feeds[int(dupi)]['title'])
    try:
        score = calc_similarity(feed_sel['title'], feeds[int(dupi)]['title'], model_w2v_AP)
    except:
        score = 0
    
    #treat as duplicates if Semantic similarity score larger than 0.85
    if score > 0.85:
        count_dup += 1
        #print(feeds[int(dupi)]['title'])
print("Number of Dupies (SimHash + WordVectors): " + str(count_dup))

Big bucket found. key:6:0, len:211
Big bucket found. key:4:2, len:260
Big bucket found. key:8:3, len:215
Big bucket found. key:10:5, len:278
Big bucket found. key:1b:6, len:205
Big bucket found. key:2:7, len:205
Big bucket found. key:0:8, len:205
Big bucket found. key:2:9, len:221


IBM Unveils z15 With Industry-First Data Privacy Capabilities
Number of duplicates (SimHash): 19
Number of Dupies (SimHash + WordVectors): 17


# Locality Sensitive Hashing implementation: Use Simhash only to deduplicate Webhose feeds based on titles

In [29]:
#Define distance, index using SimHash, calculate duplicates subset using SimHash 
distance = 10
objs = [(str(feed['id']), Simhash(str(feed['title']))) for feed in feeds]
index = SimhashIndex(objs, k=distance)

#count_dedup = 0
dedup = []
# duplicated index list
dup_index = []
for i in range(0,len(feeds)):
    if i not in dup_index:
        # Select a feed from the list based on its index
        SELECTED_INDEX = i
        feed_title = feeds[SELECTED_INDEX]
        dedup.append([SELECTED_INDEX, feed_title['title']])
        #print(SELECTED_INDEX, feed_title['title'])
        #count_dedup = count_dedup + 1
        # calculate hash value
        feed_hash = Simhash(str(feed_title['title']))
        # find all duplocate indices
        dup_indices = index.get_near_dups(feed_hash)
        #print("Number of duplicates (SimHash): " + str(len(dup_indices)))
        
        for dupi in dup_indices:
            dup_index.append(int(dupi))
            
print(len(dedup)) 

Big bucket found. key:3:0, len:389
Big bucket found. key:15:1, len:277
Big bucket found. key:7:2, len:205
Big bucket found. key:8:4, len:258
Big bucket found. key:8:5, len:281
Big bucket found. key:4:6, len:219
Big bucket found. key:14:7, len:207
Big bucket found. key:5:8, len:256
Big bucket found. key:1:0, len:230
Big bucket found. key:14:2, len:233
Big bucket found. key:0:4, len:212
Big bucket found. key:f:5, len:213
Big bucket found. key:1b:7, len:395
Big bucket found. key:7:8, len:213
Big bucket found. key:5:2, len:308
Big bucket found. key:1a:3, len:360
Big bucket found. key:19:4, len:236
Big bucket found. key:2:9, len:221
Big bucket found. key:3:0, len:389
Big bucket found. key:5:1, len:242
Big bucket found. key:8:2, len:264
Big bucket found. key:1b:6, len:205
Big bucket found. key:16:7, len:231
Big bucket found. key:3:9, len:299
Big bucket found. key:16:1, len:304
Big bucket found. key:1a:3, len:360
Big bucket found. key:11:5, len:271
Big bucket found. key:2:6, len:300
Big bucke

4786


In [30]:
print("Number of Dedupies (SimHash): " + str(len(dedup)))
print(count_dedup)

for line in dedup:
    print(line)

Number of Dedupies (SimHash): 4786
4786
[0, 'Two self-paced OpenShift Workshops for Developers']
[1, 'How Finding a Hobby Will Make You A Better Entrepreneur']
[2, 'Cognizant: Continued Strength Across Verticals, With 25% Stock Upside Likely In 2019-20 - Cognizant Technology Solutions Corporation (NASDAQ:CTSH)']
[3, 'Group Puzzles Out Silicon Specs']
[4, 'When AIs go to war: Autonomous cyber weapons ‘inevitable’']
[5, 'Tuesday Night']
[6, 'ROOMZ expands into the UK and Ireland']
[7, 'Digital skills are Africa’s ticket to prosperity']
[8, 'LevaData Announces 2019 Cognitive Sourcing Summit']
[9, 'Exeter Township woman began career in computer programming in 1962']
[10, 'Nutanix appoints new General Manager to oversee UK and Ireland']
[11, 'Why We Love Domain promo Code (And You Should, Too!)']
[12, 'Hedera Hashgraph Opens Public Network']
[13, 'Compute Express Link Consortium (CXL) Officially Incorporates; Announces Expanded Board of Directors']
[14, 'How to Personalize Digital Experienc

In [31]:
#storage file
import json
with open("LSH_duplication.json", "w") as myfile:
    for line in dedup:
        line = json.dumps(line)
        myfile.write(line)
        myfile.write("\n")

#read data from json file
json_data=open("LSH_duplication.json").readlines()
#print(json_data)

#Output: print the deduplicated subset of titles
#feeds_read_from_file = []
count=0
for line in json_data:
    count=count+1
    print(line)

print(count)
#or
print(len(json_data))

[0, "Two self-paced OpenShift Workshops for Developers"]

[1, "How Finding a Hobby Will Make You A Better Entrepreneur"]

[2, "Cognizant: Continued Strength Across Verticals, With 25% Stock Upside Likely In 2019-20 - Cognizant Technology Solutions Corporation (NASDAQ:CTSH)"]

[3, "Group Puzzles Out Silicon Specs"]

[4, "When AIs go to war: Autonomous cyber weapons \u2018inevitable\u2019"]

[5, "Tuesday Night"]

[6, "ROOMZ expands into the UK and Ireland"]

[7, "Digital skills are Africa\u2019s ticket to prosperity"]

[8, "LevaData Announces 2019 Cognitive Sourcing Summit"]

[9, "Exeter Township woman began career in computer programming in 1962"]

[10, "Nutanix appoints new General Manager to oversee UK and Ireland"]

[11, "Why We Love Domain promo Code (And You Should, Too!)"]

[12, "Hedera Hashgraph Opens Public Network"]

[13, "Compute Express Link Consortium (CXL) Officially Incorporates; Announces Expanded Board of Directors"]

[14, "How to Personalize Digital Experiences in Finan

# Semantic Similarity: add word vector-based semantic deduplication on top of LSH.

In [32]:
# list is not duplicated
sw_dedup = []
# duplicated index list
dup_index = []
for i in range(0,len(feeds)):
    if i not in dup_index:
        SELECTED_INDEX = i
        feed_title = feeds[SELECTED_INDEX]
        sw_dedup.append([SELECTED_INDEX, feed_title['title']])
        # calculate hash value
        feed_hash = Simhash(str(feed_title['title']))
        # find all duplocate indices
        dup_indices = index.get_near_dups(feed_hash)
        
        for dupi in dup_indices:
            try:
                score = calc_similarity(feed_title['title'], feeds[int(dupi)]['title'], model_w2v_AP)
            except:
                score = 0
            if score > 0.5:
                dup_index.append(int(dupi))

Big bucket found. key:3:0, len:389
Big bucket found. key:15:1, len:277
Big bucket found. key:7:2, len:205
Big bucket found. key:8:4, len:258
Big bucket found. key:8:5, len:281
Big bucket found. key:4:6, len:219
Big bucket found. key:14:7, len:207
Big bucket found. key:5:8, len:256
Big bucket found. key:1:0, len:230
Big bucket found. key:14:2, len:233
Big bucket found. key:0:4, len:212
Big bucket found. key:f:5, len:213
Big bucket found. key:1b:7, len:395
Big bucket found. key:7:8, len:213
Big bucket found. key:5:2, len:308
Big bucket found. key:1a:3, len:360
Big bucket found. key:19:4, len:236
Big bucket found. key:2:9, len:221
Big bucket found. key:3:0, len:389
Big bucket found. key:5:1, len:242
Big bucket found. key:8:2, len:264
Big bucket found. key:1b:6, len:205
Big bucket found. key:16:7, len:231
Big bucket found. key:3:9, len:299
Big bucket found. key:16:1, len:304
Big bucket found. key:1a:3, len:360
Big bucket found. key:11:5, len:271
Big bucket found. key:2:6, len:300
Big bucke

In [33]:
print("Number of Dedupies (SimHash + WordVectors): " + str(len(sw_dedup)))
print(len(sw_dedup))
for line in sw_dedup:
    print(line)

Number of Dedupies (SimHash + WordVectors): 4868
4868
[0, 'Two self-paced OpenShift Workshops for Developers']
[1, 'How Finding a Hobby Will Make You A Better Entrepreneur']
[2, 'Cognizant: Continued Strength Across Verticals, With 25% Stock Upside Likely In 2019-20 - Cognizant Technology Solutions Corporation (NASDAQ:CTSH)']
[3, 'Group Puzzles Out Silicon Specs']
[4, 'When AIs go to war: Autonomous cyber weapons ‘inevitable’']
[5, 'Tuesday Night']
[6, 'ROOMZ expands into the UK and Ireland']
[7, 'Digital skills are Africa’s ticket to prosperity']
[8, 'LevaData Announces 2019 Cognitive Sourcing Summit']
[9, 'Exeter Township woman began career in computer programming in 1962']
[10, 'Nutanix appoints new General Manager to oversee UK and Ireland']
[11, 'Why We Love Domain promo Code (And You Should, Too!)']
[12, 'Hedera Hashgraph Opens Public Network']
[13, 'Compute Express Link Consortium (CXL) Officially Incorporates; Announces Expanded Board of Directors']
[14, 'How to Personalize Dig

# Storage files 

In [34]:
import json
with open("Word2Vec_LSH_duplication.json", "w") as myfile:
    for line in sw_dedup:
        line = json.dumps(line)
        myfile.write(line)
        myfile.write("\n")

#read data from json file
json_data=open("Word2Vec_LSH_duplication.json").readlines()
#print(json_data)

#Output: print the deduplicated subset of titles using word vector-based semantic deduplication on top of LSH
#feeds_read_from_file = []
count=0
for line in json_data:
    count=count+1
    print(line)

print(count)
print(len(json_data))

[0, "Two self-paced OpenShift Workshops for Developers"]

[1, "How Finding a Hobby Will Make You A Better Entrepreneur"]

[2, "Cognizant: Continued Strength Across Verticals, With 25% Stock Upside Likely In 2019-20 - Cognizant Technology Solutions Corporation (NASDAQ:CTSH)"]

[3, "Group Puzzles Out Silicon Specs"]

[4, "When AIs go to war: Autonomous cyber weapons \u2018inevitable\u2019"]

[5, "Tuesday Night"]

[6, "ROOMZ expands into the UK and Ireland"]

[7, "Digital skills are Africa\u2019s ticket to prosperity"]

[8, "LevaData Announces 2019 Cognitive Sourcing Summit"]

[9, "Exeter Township woman began career in computer programming in 1962"]

[10, "Nutanix appoints new General Manager to oversee UK and Ireland"]

[11, "Why We Love Domain promo Code (And You Should, Too!)"]

[12, "Hedera Hashgraph Opens Public Network"]

[13, "Compute Express Link Consortium (CXL) Officially Incorporates; Announces Expanded Board of Directors"]

[14, "How to Personalize Digital Experiences in Finan